# Best Practices in TikTok Retrieval
### Jim Shepich III
### 5 December 2022

This notebook contains experiments that explore best practices in TikTok retrieval, as well as the analysis of their results.

Note: by convention, I will use decimal prefixes for file sizes (i.e. 1KB = 1000B; 1MB = 1000KB).

# Contents <a id="contents"></a>

- [Import Packages](#import-packages)
- [Corpus Processing](#corpus-processing)
- [Normalization](#normalization)
- [Combinations of Features](#features)
- [Index Construction](#index-construction)
- [Query Vectorization](#query-vectorization)
- [Cosine Scoring](#cosine-scoring)
- [Experiments](#experiments)
- [Analyses](#analyses)
    - [Index Construction & Query Time](#anal-time)
    - [Index Storage and Vocabulary Size](#anal-storage)
    - [Performance vs Query/Target Properties](#anal-queries)
    - [Performance vs Cosine Scoring Formulas](#anal-formulas)
    - [Performance vs Indexing Methodolgy](#anal-indexing)
    - [Optimal Conditions](#anal-optimal)
- [Conclusion](#conclusion)

# Import Packages <a name="import-packages"></a>
### [^Contents](#contents)

Note: all code in this assignment is implemented in Julia version 1.8.0.

In [1]:
using DataFrames #For pretty-printing results
ENV["COLUMNS"] = 10000 #Show all DataFrame columns
using Plots; plotlyjs() #For generating plots
using StatsPlots #For violin and grouped bar plots
using WebIO #Shoe plots in Notebook
using StatsBase #For basic statistical functions like mean, median, and std
using Combinatorics #For computing power sets
using BenchmarkTools #For measuring performance
using JSON #For loading data
using Unidecode #For converting emojis and Greek characters into English words
using PyCall #For accessing Python's "unidecode" library
pyunidecode = pyimport("unidecode") #For decoding other Unicode characters to ASCII
using SQLite #For saving/loading results

WebIO._IJuliaInit()

Additionally, in order to facilitate the reporting of time/memory results, I'm going to introduce a function that I've developed previously to apply a scientific prefix to a number (e.g. convert bytes to KB, MB, GB as appropriate).

In [2]:
function sciprefix(measurement::Number;maxpower=Inf)
    """Takes a measurement and determines the appropriate scientific
    prefix. The `maxpower` keyword sets the largest power that will be considered.
    """
    prefixes = [
        (18,"E"),
        (15,"P"),
        (12,"T"),
        (9,"G"),
        (6,"M"),
        (3,"k"),
        (0,""),
        (-3,"m"),
        (-6,"μ"),
        (-9,"n"),
        (-12,"p"),
        (-15,"f")
    ]
    for (power,prefix) in prefixes
        if (power>maxpower)
            continue
        end
        if measurement >= 10.0^power
            return (measurement/(10.0^power),prefix)
            #Find the first prefixed power of 10 that the
            #measurement is greater than, then return the measurement
            #in those units and that prefix.
        end
    end
end


function scifmt(measurement::Number; digits=2, unit="u", kwargs...)
    """Uses `scientific_prefix` to report a measurement with
    the appropriate scientific prefix before a specified unit abbreviation,
    rounded to a specified decimal place."""
    value, prefix = sciprefix(measurement;kwargs...)
    return "$(round(value,digits=digits)) $(prefix)$(unit)"
end

scifmt (generic function with 1 method)

# Corpus Processing <a id="corpus-processing"></a>
### [^Contents](#contents)

The data we will use in these experiments are derived from a small collection of TikToks that I scraped from my bank of liked videos. Details on the scraping process are provided in `README.md`. Specifically, we will be studying text data extracted from the TikToks; after cleaning and processing, this data is stored in `data/clean_master.json`. Each TikTok contains the following text fields for potential indexing:

- Basic information: creator username and nickname, description text (including hashtags), audio title
- Comment text and commenter usernames
- Text extracted from the coverphoto using OCR
- Text extracted from the audio using speech recognition

In [3]:
TIKTOKS = JSON.parsefile("data/cleaned_master.json",use_mmap=false)
for tiktok in values(TIKTOKS)
    tiktok["comment-text"] = join([comment["comment-text"] for comment in tiktok["comments"]]," ")
end
println("Corpus size: $(length(TIKTOKS)) documents ($(scifmt(Base.summarysize(TIKTOKS),digits=2,unit="B")))")

Corpus size: 1462 documents (23.99 MB)


# Normalization <a id="normalization"></a>
### [^Contents](#contents)

One primary focus of our experiments will be different methods of tokenization: words vs character n-grams of varying length. We will construct a normalization function that can do either.

Exploratory analysis reveals that TikTok descriptions and comments are rife with Unicode characters, including emojis, characters from foreign languages (Japanese is especially common among these TikToks as it is my second language), bold/italic/cursive letters, and other miscellaneous characters.

The `Unidecode.jl` library converts emojis, Greek characters, and a small handful of other characters into English words describing the character; for example "😅" is unidecoded to ":sweat_smile:" and "α" is unidecoded to "alpha."

We will additionally use the `unidecode.py` Python library (via PyCall), which does not handle emojis, and decodes Greek characters to English letters instead of their names (e.g. "α" is decoded to "a" instead of "alpha"), but otherwise has a much broader range of applicability. Notably, it can decode Japanese characters to romaji (Latin characters), which will be important for  handling the few Japanese documents in the corpus, and it will ensure that the output is strictly ACSII.

So, in order to ensure that we do not lose the emojis, we will use `Unidecode.jl` first, and then `unidecode.py`.

In [4]:
function normalize(document::String; 
        delim=r"[\s/—-]+",
        replacements=[(r"[\s/—-]+"," "), (r"[^\w@# ]",""), (!isascii,"")],
        case_folding=lowercase,
        filters = [token -> token==""],
        stopwords = Set(),
        ngram_size = nothing
    )
    """This function normalizes a text document, generating an array of
    tokens by the following process:
    
    1. Decode Unicode characters and apply the specified `case_folding` function.
    2. If n-grams size is not specified, use word tokenization:
        2.1 Split on the specified delimiter (`delim`).
        2.2 Apply the specified `replacements` to each token.
    3. If n-gram size is specified, use n-gram tokenization:
        3.1 Apply `replacements` to the entire document string.
        3.2 Tokenize by generating each consecutive `ngram_size`-sized substring.
    4. Apply the list of `filter` functions and remove invalid tokens and `stopwords`.
    """
    document = unidecode(document)
    #Use Unidecode.jl to decode emojis and Greek characters.
    document = pyunidecode.unidecode(document)
    #Use unidecode.py to decode the rest of the Unicode characters.
    document = case_folding(document)
    #Perform case folding.
    
    
    tokens = String[]
    if isnothing(ngram_size)
        #If an n-gram size is not specified, then use word tokenization.
        for token in split(document,delim)
            #Split the text on the delimiters.
            for (pattern, replacement) in replacements
                token = replace(token, pattern => replacement)
            end
            #Perform all specified replacements.
            push!(tokens,token)
        end
    else
        #Otherwise, use n-gram tokenization.
        for (pattern, replacement) in replacements
            document = replace(document, pattern => replacement)
        end
        #With n-gram tokenization, replacements are done on the entire document.
        if length(document) < ngram_size
            #If the n-gram size is larger then the document, then just treat it as blank.
        else 
            tokens = String[
                join(document[i:j]) for (i,j) in
                zip(1:(length(document)-ngram_size+1),ngram_size:length(document)+1)
            ]
        end
    
    end
    
    
    valid_tokens = [token for token in tokens 
            if !(any(filter(token) for filter in filters)||(token in stopwords))]
    #Only keep tokens that survive all the filters and are not stopwords.
    
    return valid_tokens
end

normalize (generic function with 1 method)

Regardless of tokenization, I will fold to lower-case, and I won't remove any stopwords. 

With word tokenization, I will use the `[\s/—-]+` pattern as the delimiter to split on any number of consecutive spaces, forward-slashe, em-dashes, or hyphens. With n-gram tokenization, I will replace matches to this pattern with a single space in order to have a single character to break up alphanumerics.

All non-alphanumeric characters other than spaces, the @ symbol (used to denote usernames), and the # symbol (used in hashtags) will be removed. I will include a filter to catch empty tokens, as that can be an issue with the post-splitting replacement procedure used in word-tokenization.

# Combinations of Features <a id="features"></a>
### [^Contents](#contents)

Another central focus of this research will be to identify which types of information are useful to include in the index. To this end, I will try enriching the base data with each of the 8 members of the power set of {title OCR text, speech recognition text, comment text} to see what conditions yield the best results. 

My hypothesis is that speech recognition and title OCR text will always be useful when they are available; comment text will be helfpul for content that is more nonverbal, but may be detrimental to overall results because they are often off-topic.

Additionally, we will examine whether or not attributing terms to the fields from which they were derived will help. I think that the potential benefit of this is that it could prevent small n-grams in the basic information from being drowned out by occurrences of that same n-gram in a lower-quality field (i.e. comments, which are spammier than the other fields). It's worth noting that usernames and hashtags somewhat have their own built-in form of field attributions. Query terms will be tried against each field; the only benefit would be the increase in IDF in the document vector by splitting components by field of origin.



In [5]:
function attribute_field(tokens::Vector{String},fieldname::String)
    """Prefix each token with the fieldname and a colon."""
    return String["$(fieldname)$(token)" for token in tokens]
end


function attribute_all_fields(query_tokens::Vector{String})
    """Prefix each query token with every attirbution label so that
    postings from all fields can be used to compute similarity."""
    
    return vcat(
        query_tokens,#No prefix for basic info.
        String["ocr:$(token)" for token in query_tokens],
        String["sr:$(token)" for token in query_tokens],
        String["c:$(token)" for token in query_tokens]
    )
    
end

BASIC_FIELDS = ["creator-username","creator-nickname","description","music-title"]
ATTRIBUTION_PREFIXES = Dict(
    "speech-to-text" => "sr:",
    "coverphoto-ocr" => "ocr:",
    "comment-text" => "c:"
);

# Index Construction <a id="index-construction"></a>
### [^Contents](#contents)

Now, we have to implement the memory-based inversion algorithm. The function needs a few minor adjustments for this study because the docIDs are strings instead of integers, and we need to loop over multiple fields, possibly adding attribution prefixes. Otherwise, this is pretty straightforward.

In [6]:
function inverted_file_index(corpus::Dict; attributions=Dict(),fields=BASIC_FIELDS, norm_kwargs...)
    """This function constructs an inverted file index for an input corpus. The output 
    is a Dict of (term, postings list) pairs, where each postings list is a vector of 
    (docID, term frequency) pairs.
    
    The `fields` keyword specifies which fields of the corpus to index, and the `attributions`
    keyword is used to assign respective field attribution prefixes, if any.
    """
    index = Dict{String,Vector{Tuple{String,Int}}}()
    #Initialize the index as an ordered dict that maps each term in the corpus 
    #to a postings list, which is a vector containing (docID, term frequency) pairs.
    
    for (id, document) in corpus
        term_frequencies = Dict{String,Int}()
        #Count each term as it occurs in the document.
        for field in fields
            for term in attribute_field(
                    normalize(document[field]; norm_kwargs...),get(attributions,field,""))
                #Normalize the raw document; apply the specified field attribution prefix.
                if haskey(term_frequencies,term)
                    term_frequencies[term] += 1
                else
                    term_frequencies[term] = 1
                end
                #Tally each term as it appears in the normalized sequence of terms.
            end
        end

        for (term,term_frequency) in term_frequencies
            if haskey(index,term)
                push!(index[term], (id,term_frequency))
            else
                index[term] = [(id,term_frequency)]
            end
            #If the term is already in the index, simply add a posting for this 
            #document. Otherwise, initialize the postings list with this posting.
        end  
        
    end
    return index
end

inverted_file_index (generic function with 1 method)

# Query Vectorization <a id="query-vectorization"></a>
### [^Contents](#contents)

I'll start by loading the queries from `queries.json`, which is formatted as a list of objects.

In [7]:
QUERIES = JSON.parsefile("queries.json",use_mmap=false)
println("Number of test queries: $(length(QUERIES))")

Number of test queries: 86


In [8]:
db = SQLite.DB("results.db")
DBInterface.execute(db,"DELETE FROM queries;")
DBInterface.close!(db)
db = SQLite.DB("results.db")
for (q_id,query) in enumerate(QUERIES)
    try
    ranking_results = DBInterface.execute(db,"""
        INSERT INTO queries(query_id,query_text,target_id,author,useful_description,
            comments_on_topic,purely_visual,important_lyrics,subtextual)
        VALUES (?,?,?,?,?,?,?,?,?)""",(
            q_id, query["text"], query["target"], query["author"], query["useful-description"],
            query["comments-on-topic"],query["purely-visual"],query["important-lyrics"],
            query["subtextual"]
        ))
    catch e
        println(e)
        println(query)
    end
end
DBInterface.close!(db)

The last aspect we will focus on in our experiments is how cosine scoring is performed. Going forward, the notation I will use for different term weighting factors is consistent with that in [_Term-weighting approaches in automatic text retrieval_ (DOI: 10.1016/0306-4573(88)90021-0)](https://www.sciencedirect.com/science/article/abs/pii/0306457388900210).


Most queries will likely be short and not meaningfully use any term more than once, so I think it is reasonable to assume that binary weighting on query terms will be fine. Normalization of the query vector doesn't matter because it will simply scale every score by the same factor, meaning the ranking will be unaffected. I will opt to normalize, so that the results will be between 0 and 1 when the document vector is also normalized, which will lend itself to interpretability.

All of this is to say that we'll use the same formula (bxc) for weighting terms in query vectors. Our experimentation will only vary term weighting methods for document vectors.

In [9]:
function vectorize_query(query_tokens::Vector{String};
        formula=(:b,:x,:c),n_docs=1,index=nothing,norm_kwargs...)
    """This function parses a query string as a term-space vector. The 
    `formula` keyword argument specifies which choice of term frequency, collection
    frequency, and normalization factors to use when calculating the vector's components.
    
    If idf or probabilistic inverse collection frequency are used as the collection 
    frequency factor, then the number of documents in the target corpus and an inverted
    index of the target corpus must be passed as keyword arguments.
    """
    vector = Dict()
    if formula[1] == :b
        vector = Dict(term => 1.0 for term in unique(query_tokens))
        #With binary weighting, each term that occurs gets a this-document factor of 1.
    elseif formula[1] == :t
        vector = countmap(query_tokens)
        #With tf weighting, each term gets a this-document factor equal to the number
        #of times it occurs.
    elseif formula[1] == :n
        count_map = countmap(query_tokens)
        max_tf = maximum(values(count_map))
        #Get the maximum tf for augmented normalized tf weighting.
        vector = Dict(term => 0.5*(1+tf/max_tf) for (term,tf) in count_map)
        #Use the formula for augmented normalized tf weighting.
    end
    
    if formula[2] == :x
        #If the collection factor is just 1, we don't need to do anything.
    elseif formula[2] == :f
        vector = Dict(
            term => component * log2(n_docs/length(get(index,term,[])))
            for (term, component) in vector
        )
        #The collection-frequency factor is equal to idf, which is the base-2
        #log of the total number of documents divided by the number of documents
        #that term occurs in.
    elseif formula[2] == :p
        vector = Dict(
            term => component * log2(
                (n_docs-length(get(index,term,[])))/length(get(index,term,[]))
            )
            for (term, component) in vector
        )
        #Probabilistic inverse collection frequency just involves subtracting the
        #df from the total number of documents (the numerator of the idf expression)
    end
    
    if formula[3] == :x
        #No normalization
    elseif formula[3] == :c
        normalization_factor = sqrt( sum(component^2 for component in values(vector)) )
        vector = Dict(key => value/normalization_factor for (key, value) in vector)
        #Divide each component by the magnitude of the vector.
    end
    
    return vector
end

vectorize_query (generic function with 1 method)

# Cosine Scoring <a id="consine-scoring"></a>
### [^Contents](#contents)

In order to perform cosine scoring with normalization, we need to compute lengths of document vectors. Instead of doing this once per query, we only need to do it once per experiment (every time the index and/or document vector weighting formula change). So, I've implemented a function that will perform this calculation so we can store the results.

Note: because augmented normalized term frequency weighting (the :n term weight) requires computing max term frequency for every document, which is a bit convoluted, I've opted to exclude it from our study.

In [10]:
function document_vector_lengths(index::Dict, corpus_size::Int;formula=(:t,:f,:x))
    """This function computes for each document in a corpus the magnitude of the term-space 
    vector of that document.
    
    The `formula` keyword argument specifies which choice of term frequency, collection
    frequency, and normalization factors to use when calculating the vector's components."""
    vector_lengths = Dict{String,Float64}()
    
    for (term,postings) in index
        for (docid,tf) in postings
            component = 0
            if formula[1] == :b
                component = 1
            elseif formula[1] == :t
                component = tf
            end
            #Term weighting factor.
            
            if formula[2] == :x
            elseif formula[2] == :f
                component *= log2(corpus_size)/length(postings)
            elseif formula[2] == :p
                component *= log2(
                    (corpus_size-length(postings))/length(postings)
                )
            end 
            #Document weighting factor.
            
            if docid ∈ values(vector_lengths)
                vector_lengths[docid] += component^2
            else 
                vector_lengths[docid] = component^2
            end
            #For each docid, we must first compute the sum of squared components. 
        end
    end
    return Dict{String,Float64}(docid => sqrt(sum_sq) for (docid,sum_sq) in vector_lengths)
    #Take the square root of the sum of squared term-frequency components.
end

document_vector_lengths (generic function with 1 method)

The following function performs cosine scoring and returns a ranked list of docids.

In [11]:
function cosine_score(
        query_tokens::Vector{String}, index::Dict, corpus_size::Int;
        query_formula = (:b,:x,:c), document_formula = (:t,:f,:c),
        document_veclengths=nothing
    )
    """This function computes vector similarity scores between a query and a corpus
    and returns list of docids, sorted in rank order.
    
    The `query_formula` and `document_formula` keyword arguments specify how term-space
    vector components for the query and the documents in the corpus are computed, using
    the notation provided by Salton and Buckley.
    
    Vector-magnitude normalization requires vector lengths for each corpus document. These 
    can be passed as keyword arguments to save time, or can be computed on-the-fly otherwise.
    """
    
    query_vector = vectorize_query(query_tokens,formula=query_formula,index=index,n_docs=corpus_size)
    #Parse the query into a term-space vector.
    
    sim_scores = Dict{String,Float64}()
    
    for (term, q_component) in query_vector
        #Loop over each term in the query vector.
        for (docid,tf) in get(index,term,[])
            #Compute the term-space vector component corresponding
            #to the given term for each document in that term's postings list.
            if (document_formula[2]==:f)&&(document_veclengths[docid]==0)
                continue
                #Skip documents with length 0.
            end
            d_component = 0
            if document_formula[1] == :b
                d_component = 1
                #If the docid is in the postings list, then the term must be 
                #present in the document.
            elseif document_formula[1] == :t
                d_component = tf
                #Tf weighting.
            end
            #Compute the term frequency factor.
            
            if document_formula[2] == :x
                #No collection frequency weighting.
            elseif document_formula[2] == :f
                d_component *= log2(length(document_veclengths)/length(get(index,term,[])))
                #Multiply by the idf.
            elseif document_formula[2] == :p
                d_component *= log2(
                    (length(document_veclengths)-length(get(index,term,[])))/length(get(index,term,[]))
                )
                #Multiply by the idf. 
            end 
                
            if document_formula[3] == :x
                #No normalization.
            elseif document_formula[3] == :c
                d_component /= document_veclengths[docid]
                #Divide by the length of the document's term-space vector.
            end
            
            if docid in keys(sim_scores)
                sim_scores[docid] += q_component*d_component
            else
                sim_scores[docid] = q_component*d_component
            end
            #Multiply the corresponding component of the query and document's 
            #term-space vectors together and add to the running total (similarity score).
            
            
        end
    end
    
    return sort!(collect(keys(sim_scores)), by=(docid->sim_scores[docid]), rev=true)
    #Sort the similarity scores in decreasing order.
        
end

cosine_score (generic function with 1 method)

# Experiments <a id="experiments"></a>
### [^Contents](#contents)

Now all that's left is to run the experiments. To quickly recap what's been discussed so far, we comparing the following methodologies:

- n-gram vs word tokenization (including n-gram size)
    - Because documents are relatively short, they're less likely to have multiple morphological variants of a given word. Additionally, because these data are obtained from social media, they are more likely to have spelling errors. These factors both suggest that n-gram tokenization may be more helpful.
- Combinations of different features: basic + 2^{speech to text, coverphoto ocr, comment text}
    - Comments may help provide context to videos with little to no recognizable speech and/or sparse description. However, it's possible that off-topic comments may cause irrelevant documents to rank higher, reducing precision. We expect Coverphoto OCR and speech recognition to always be helpful (or never harmful at the least).
- Field attribution (i.e. labeling terms based on which feature they were derived from)
    - We have set it up such that queries will match with a term regardless of which feature it came from, so field attributions will only have an impact on a document term's IDF. We expect that this should help mitigate the negative impact of off-topic comment text, which tends to be more verbose than the basic information.


Additionally, we will examine the following methods for computing document vector components:
- Raw (:t) vs binary (:b) term weighting
    - Possible that :b is more useful because :t will be biased toward longer videos
- None (:x) vs IDF (:f) vs probabilistic IDF (:p)
    - Most likely that :f or :p is best because they give higher weight to rarer terms
- None (:x) vs Euclidean (:c) normalization
    - Possible that :x is better than :c if documents are diluted by long, useless comments


There are two common use-cases for TikTok retrieval: searching for an individual TikTok that a user vaguely remembers but lost track of, and searching for TikToks related to a trend or theme. The platform's search engine usually works pretty well in the latter case; our goal is to improve the former. In other words, we are trying to optimize the ability to recall specific videos.

The test queries were constructed to this end, and they thus only have a single relevant retrieval target. Because we are only dealing with a single relevant document for each query, the metric we will use to evaluate performance is the average rank of the target in the similarity-ranked list. In the best case, this metric will be close to 1. If the retrieval system were to rank documents at random, we would expect the metric to be around ~731 (the midpoint of the list). If the metric is close to 1462, then we are probably sorting the ranked list backwards.

In [12]:
ngram_sizes = [nothing,4,5,6,7]
features = collect(powerset(["speech-to-text","comment-text","coverphoto-ocr"]))
index_iterator = Iterators.product(ngram_sizes,[true,false],features)
println("$(length(index_iterator)) indices to be generated")

formula_iterator = Iterators.product([:b,:t],[:x,:f,:p],[:x,:c])
println("$(length(formula_iterator)) combinations of scoring formulas to be used on each")


println("$(length(formula_iterator)*length(index_iterator)) total experiments to be performed")

80 indices to be generated
12 combinations of scoring formulas to be used on each
960 total experiments to be performed


In [13]:
RUN_EXPERIMENTS = false;
#Toggles whether to run the experiments or skip to the analysis 
#(in case you refresh the notebook).

Finally, before we run the experiments, we should run each of the function once to pre-compile them so that the `@time` estimates are accurate (otherwise, they will include compile time for the first experiment).

In [14]:
if RUN_EXPERIMENTS
        throwaway_index = inverted_file_index(
            TIKTOKS; 
            attributions = Dict(),
            fields = BASIC_FIELDS, 
            ngram_size = nothing
        )
    
        ranked_list = cosine_score(normalize("luffy"), throwaway_index,
            length(TIKTOKS);document_formula = (:t,:x,:x))
    
        println(ranked_list)
end

Without further ado, let's run the experiments.

In [15]:
if RUN_EXPERIMENTS
@time begin    
n_indices = length(index_iterator)
n_experiments = n_indices * length(formula_iterator)
experiment_id = 0
CORPUS_SIZE = length(TIKTOKS)

db = SQLite.DB("results.db")
DBInterface.execute(db,"DELETE FROM indexes;")
DBInterface.execute(db,"DELETE FROM experiments;")
DBInterface.execute(db,"DELETE FROM ranking_results;")
#Erase old results.

for (index_id,(ngram_size,attributions,features)) in enumerate(index_iterator)
    
    println("Experimenting on index $(index_id) / $(n_indices)")
    
    index = nothing
    
    indexing_time = @elapsed begin
        index = inverted_file_index(
            TIKTOKS; 
            attributions = attributions ? ATTRIBUTION_PREFIXES : Dict(),
            fields = vcat(BASIC_FIELDS,features), 
            ngram_size = ngram_size
        )
    end
    
    
    DBInterface.execute(
        db,
        """INSERT INTO indexes(index_id,ngram_size,field_attributions,sr,ocr,
        comments,indexing_time,storage,vocab_size)
        VALUES (?,?,?,?,?,?,?,?,?);""",
        [index_id,ngram_size,attributions,("speech-to-text"∈features),("coverphoto-ocr"∈features),
        ("comment-text" ∈ features), indexing_time, Base.summarysize(index),length(index)]
    )
    
    normalized_queries = [
        (attributions ? attribute_all_fields(normalize(query["text"];ngram_size=ngram_size)) : 
            normalize(query["text"];ngram_size=ngram_size), query["target"])
        for query in QUERIES
    ]
    #If the index uses field attributions, ensure that the query search for matches in all fields.
    
    
    for (term_weight,collection_weight,normalizer) in formula_iterator
        experiment_id += 1
         DBInterface.execute(
            db,
            """INSERT INTO experiments(experiment_id,index_id,term_weight,
            collection_weight,normalizer) VALUES (?,?,?,?,?);""",
            [experiment_id, index_id, string(term_weight),
                string(collection_weight), string(normalizer)]
        )
        
        document_veclengths = document_vector_lengths(index, CORPUS_SIZE;
            formula=(term_weight,collection_weight,normalizer))
        
        for (query_id,(query_tokens, target_id)) in enumerate(normalized_queries)
            
            target_rank = Inf
            retrieval_time = @elapsed begin
                
                ranked_list = cosine_score(query_tokens, index, CORPUS_SIZE;
                    document_formula = (term_weight,collection_weight,normalizer),
                    document_veclengths=document_veclengths)
                    target_rank = findfirst(ranked_list.==target_id)
            
            end
            
            DBInterface.execute(
            db,
            """INSERT INTO ranking_results(experiment_id,query_id,retrieval_time,target_rank) 
                VALUES (?,?,?,?);""",
            [experiment_id, query_id, retrieval_time, target_rank]
        )
        end
        
    end
       
end


DBInterface.close!(db)
end    
end

`4028.811022 seconds (3.50 G allocations: 126.479 GiB, 1.00% gc time, 0.05% compilation time: 1% of which was recompilation)`

# Analyses <a id="analyses"></a>
### [^Contents](#contents)

In this section, we'll take a look into the results. Note: there were several cases in which retrieval targets were not included in the ranked list returned by cosine scoring (indicating that the queries were unsuccessful) so a NULL value was logged. We cannot simply skip these results; failing to appear in the ranked list should negatively impact the performance metric. That said, we cannot quantify how bad the failure is. I propose that we interpolate these missing ranked results with 731, which is the midpoint of the ranked list --- the expected rank if the retrieval system were to assign the documents random ranks. I believe that this is a fair penalty, as it effectively treats a failed retrieval as the average case of the null model rather than the worst-case.



In [16]:
sql = Dict{Symbol,String}()

sql[:ranking_results] = """
    SELECT * FROM ranking_results 
    RIGHT JOIN queries ON ranking_results.query_id = queries.query_id""";
#Obtain ungrouped ranking results so we can make violin plots of average rank.

sql[:expt_avgs] = """
    SELECT experiments.index_id, experiments.experiment_id, experiments.term_weight,
        experiments.collection_weight, experiments.normalizer,
        AVG(ranking_results.retrieval_time) as avg_query_time,
        AVG(COALESCE(ranking_results.target_rank,731)) as avg_rank 
    FROM experiments RIGHT JOIN ranking_results 
        ON experiments.experiment_id = ranking_results.experiment_id
    GROUP BY experiments.experiment_id""";
#Computes the average rank and query time over all queries for a given experiment.


sql[:index_results] = """
    SELECT indexes.index_id, ngram_size, sr, ocr, comments, field_attributions,
        indexing_time, storage, vocab_size, AVG(avg_query_time) as index_avg_query_time, 
        AVG(avg_rank) as index_avg_rank
    FROM indexes LEFT JOIN ($(sql[:expt_avgs])) avg_ranking
        ON indexes.index_id = avg_ranking.index_id
    GROUP BY indexes.index_id""";
#Averages results from all experiments performed with a single index.


sql[:formula_avgs] = """
    SELECT experiment_id, term_weight, collection_weight, normalizer,
    AVG(avg_rank) as formula_avg_rank FROM ($(sql[:expt_avgs])) expt_avgs
    GROUP BY term_weight, collection_weight, normalizer
""";
#Groups average experiment results by formula (combining results from different indices).


## Index Construction & Query Time <a id="anal-time"></a>
### [^Contents](#contents)

In [17]:
db = SQLite.DB("results.db")
indexes = DBInterface.execute(db,sql[:index_results]) |> DataFrame
DBInterface.close!(db)
println(size(indexes))
first(indexes,3)

(80, 11)


3×11 DataFrame
 Row │ index_id  ngram_size  sr     ocr    comments  field_attributions  indexing_time  storage   vocab_size  index_avg_query_time  index_avg_rank 
     │ Int64     Int64?      Int64  Int64  Int64     Int64               Float64        Int64     Int64       Float64               Float64        
─────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │        1     missing      0      0         0                   1       0.421693   2634195       11272           0.000453285         515.886
   2 │        2           4      0      0         0                   1       0.785864   8611190       37831           0.000889729         204.906
   3 │        3           5      0      0         0                   1       0.541532  13734735       69873           0.000348217         256.664

We'll start out by looking at a simple histogram of all the index construction times to get a sense of the distribution.

In [18]:
p1 = histogram(
    indexes[:,"indexing_time"],
    title="Index Construction Time",
    xlabel="Time (s)",
    ylabel="Count",
    bins= minimum(indexes[:,"indexing_time"]):1:maximum(indexes[:,"indexing_time"]),
    legend=false
)

p2 = histogram(
    indexes[:,"index_avg_query_time"],
    title="Average Query Time",
    xlabel="Time (s)",
    ylabel="Count",
    legend=false
)

plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Distribution of Run Times")

These distributions appear notably bimodal. I have a feeling that including extra sources of text is probably to blame. Let's see if that's the case.

In [19]:
sr_mask = (indexes[:,"sr"].==1)
ocr_mask = (indexes[:,"ocr"].==1)
c_mask = (indexes[:,"comments"].==1)


p1 = bar(
    [
        mean(indexes[(!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"indexing_time"]),
        mean(indexes[(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"indexing_time"]),
        mean(indexes[(!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),"indexing_time"]),
        mean(indexes[(!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),"indexing_time"]),
        mean(indexes[(sr_mask).&&(ocr_mask).&&(!).(c_mask),"indexing_time"]),
        mean(indexes[(sr_mask).&&(!).(ocr_mask).&&(c_mask),"indexing_time"]),
        mean(indexes[(!).(sr_mask).&&(ocr_mask).&&(c_mask),"indexing_time"]),
        mean(indexes[(sr_mask).&&(ocr_mask).&&(c_mask),"indexing_time"])
    ],
    xticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    title = "Index Construction Time",
    xlabel = "Feature",
    ylabel = "Time (s)",
    legend = false
)

p2 = bar(
    [
        mean(indexes[(!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"index_avg_query_time"]),
        mean(indexes[(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"index_avg_query_time"]),
        mean(indexes[(!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),"index_avg_query_time"]),
        mean(indexes[(!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),"index_avg_query_time"]),
        mean(indexes[(sr_mask).&&(ocr_mask).&&(!).(c_mask),"index_avg_query_time"]),
        mean(indexes[(sr_mask).&&(!).(ocr_mask).&&(c_mask),"index_avg_query_time"]),
        mean(indexes[(!).(sr_mask).&&(ocr_mask).&&(c_mask),"index_avg_query_time"]),
        mean(indexes[(sr_mask).&&(ocr_mask).&&(c_mask),"index_avg_query_time"])
    ],
    xticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    title = "Average Query Time",
    xlabel = "Feature",
    ylabel = "Time (s)",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Run Times vs Additional Features")

Interestingly, it appears that comments have the strongest impact on indexing time; enriching the basic information with comments alone results in a >5x increase in the time it takes to index the corpus, nearly ~2.5x more than if we enrich with both speech recognition and optical character recognition. This trend is certainly also present in average query time, but the differences are less pronounced. We will probably see a similar trend in index storage and query time as wee see here. 

For the time being, let's take a quick look at how n-gram size impacts indexing time if it does at all. 

In [20]:
nogram_mask = (ismissing.(indexes[:,"ngram_size"]))
gram4_mask = coalesce.(indexes[:,"ngram_size"].==4,false)
gram5_mask = coalesce.(indexes[:,"ngram_size"].==5,false)
gram6_mask = coalesce.(indexes[:,"ngram_size"].==6,false)
gram7_mask = coalesce.(indexes[:,"ngram_size"].==7,false)
#Bitwise operators on missing values return missing, so we fill them in with false.


p1 = bar(
    [
        mean(indexes[nogram_mask,"indexing_time"]),
        mean(indexes[gram4_mask,"indexing_time"]),
        mean(indexes[gram5_mask,"indexing_time"]),
        mean(indexes[gram6_mask,"indexing_time"]),
        mean(indexes[gram7_mask,"indexing_time"])
    ],
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    title = "Index Construction Time",
    xlabel = "Method",
    ylabel = "Time (s)",
    legend = false
)

p2 = bar(
    [
        mean(indexes[nogram_mask,"index_avg_query_time"]),
        mean(indexes[gram4_mask,"index_avg_query_time"]),
        mean(indexes[gram5_mask,"index_avg_query_time"]),
        mean(indexes[gram6_mask,"index_avg_query_time"]),
        mean(indexes[gram7_mask,"index_avg_query_time"])
    ],
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    title = "Average Query Time",
    xlabel = "Method",
    ylabel = "Time (s)",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Run Times vs Tokenization Method")

N-gram size appears to have some positive effect on indexing time; this may reflect sub-optimal hash table performance resulting from an increased vocabulary size. Average query time has a much different trend; we see a huge spike for 4-grams; this likely reflects an increased pool of candidate matches for which cosine scores must be calculated. This probably arises from the smaller vocabulary size of the 4-gram index (a lot more documents will match a 4-gram than a 7-gram from the query).

Finally, let's take a look at a heatmap comparing tokenization method and enriching features (if this looks good, it will save us some time in the next few sections).

In [21]:
indexing_time_vs_tokenization_and_features = [
    mean(indexes[feature_mask.&&tokenization_mask,"indexing_time"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]

index_avg_query_time_vs_tokenization_and_features = [
    mean(indexes[feature_mask.&&tokenization_mask,"index_avg_query_time"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]



p1 = heatmap(
    indexing_time_vs_tokenization_and_features,
    yticks = (1:8, ["basic","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Index Constuction Time",
    ylabel = "Features",
    xlabel = "Tokenization"
)

p2 = heatmap(
    index_avg_query_time_vs_tokenization_and_features,
    yticks = (1:8, ["basic","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Average Query Time",
    ylabel = "Features",
    xlabel = "Tokenization"
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Run Times vs Tokenization & Extra Features")

It appears that the effects of extra features and tokenization are more or less independent of each other, which is good to know. The effect of tokenization and extra features on index construction time are on the same order of magnitude, whereas tokenization exerts a much heavier influence on query time. 

Finally, let's see if field attributions made much of a difference.

In [22]:
attribution_mask = (indexes[:,"field_attributions"].==1)

p1 = bar(
    [
        mean(indexes[(!).(attribution_mask),"indexing_time"]),
        mean(indexes[(attribution_mask),"indexing_time"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "Index Construction Time",
    xlabel = "Field Attributions",
    ylabel = "Time (s)",
    legend = false
)

p2 = bar(
    [
        mean(indexes[(!).(attribution_mask),"index_avg_query_time"]),
        mean(indexes[(attribution_mask),"index_avg_query_time"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "Average Query Time",
    xlabel = "Field Attributions",
    ylabel = "Time (s)",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Run Times vs Field Attributions")

The index construction time is nearly the same, which makes sense, since the same amount of text is indexed regardless of whether field attributions are used or not. On the other hand, queries take slightly longer when field attributions are used. Again, this probably reflects decreased hash table efficiency due to larger vocabulary size.

## Index Storage and Vocabulary Size <a id="anal-storage"></a>
### [^Contents](#contents)

Next, we'll examine how the index construction methodologies affect index size, both in terms of memory usage and vocabulary size.

In [23]:
storage_vs_tokenization_and_features = [
    mean(indexes[feature_mask.&&tokenization_mask,"storage"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]

vocab_size_vs_tokenization_and_features = [
    mean(indexes[feature_mask.&&tokenization_mask,"vocab_size"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]


p1 = heatmap(
    storage_vs_tokenization_and_features,
    yticks = (1:8, ["basic","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Index Memory Usage",
    ylabel = "Features",
    xlabel = "Tokenization"
)

p2 = heatmap(
    vocab_size_vs_tokenization_and_features,
    yticks = (1:8, ["basic","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Vocabulary Size",
    ylabel = "Features",
    xlabel = "Tokenization"
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Index Size vs Tokenization & Extra Features")

Unsurprisingly, memory consumption and vocabulary size both increase as we enrich the basic information with more text and as we use larger n-grams, which result in more unique terms.

In [24]:
attribution_mask = (indexes[:,"field_attributions"].==1)

p1 = bar(
    [
        mean(indexes[(!).(attribution_mask),"storage"]),
        mean(indexes[(attribution_mask),"storage"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "Index Memory Usage",
    xlabel = "Field Attributions",
    ylabel = "Size (B)",
    legend = false
)

p2 = bar(
    [
        mean(indexes[(!).(attribution_mask),"vocab_size"]),
        mean(indexes[(attribution_mask),"vocab_size"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "Vocabulary Size",
    xlabel = "Field Attributions",
    ylabel = "Number of Terms",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Index Size vs Field Attributions")

Field attributions only yield a slight increase in memory usage but a somewhat more pronounced increase in vocabulary size. This may indicate that the number of postings is largely conserved, meaning that terms that are distinguished by field attributions may occur in different documents. Although there is some increase increase in vocabulary size, it is small relative to the maximum 4x increase that would result if every term occurred at least once in every field. This may indicate that there is not much lexical overlap between the different information fields. If this is the case, then it bodes well for the increase in performance we hope to see from enriching the basic text. 

## Performance vs Query/Target Properties <a id="anal-queries"></a>
### [^Contents](#contents)

Now, we will begin our analysis of retrieval performance. We will start out by examining how various properties of the queries influence the performance of ranked retrieval.

In [25]:
db = SQLite.DB("results.db")
ranking_results = DBInterface.execute(db,sql[:ranking_results]) |> DataFrame
DBInterface.close!(db)
println(size(ranking_results))
first(ranking_results,3)

(82560, 13)


3×13 DataFrame
 Row │ experiment_id  query_id  retrieval_time  target_rank  query_id_1  query_text                    target_id            author  useful_description  comments_on_topic  purely_visual  important_lyrics  subtextual 
     │ Int64          Int64     Float64         Int64?       Int64       String                        String               String  Int64               Int64              Int64          Int64             Int64      
─────┼─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │             1         1        0.189629            1           1  D&D players stairs door       7171982974357966122  jim                      0                  1              0                 0           0
   2 │             1         2        7.6e-5        missing           2  knight besties sword fight    7144411926246935854  jim                      0                  1              1                 0           0
   3 │             1         3        7.36e-5       missing           3  football dad musical theater  7052789831151193391  jim                      1                  1              0                 0           0

First, we will use violin plots to get a sense the quality/success of each individual query. High-quality queries should have violin plots that are widest around 1. Low-quality queries will have violins that are widest around 731, which indicates failure to retrieve the relevant TikTok. Violins that are large over a wider range of ranks correspond to queries whose success is strongly influenced by the retrieval methodology.

In [26]:
for author in unique(ranking_results[:,"author"])
    author_mask = (ranking_results[:,"author"].==author)
    author_ids = unique(ranking_results[author_mask,"query_id"])
    
    plot = violin(
        [coalesce.(ranking_results[
                    author_mask.&&(ranking_results[:,"query_id"].==q_id),"target_rank"],731)
            for q_id in author_ids],
        x_ticks = (1:length(author_ids),["Q$(i)" for i in author_ids]),
        color = theme_palette(:auto)[1],
        legend = false,
        ylabel="Rank of Target",
        title="Distribution of Ranks over All Experiments - $(titlecase(author))'s Queries",
        size=(900,300)
    )
    
    display(plot)
    
end
    

These plots contian a lot of information. First off, we can see that the majority of queries are high quality, with the brunt of their density around low-numbered ranks. 

Next, we notice that query quality is somewhat influenced by author. Particularly, Huey, Anvesha, and Emily's queries tended to be more difficult than mine, Jack's, or Sam's. 

Many of the violins are bimodal around 1 and 731, which indicates that the **retrieval methodology really is worth investigating because it can mean the difference between ranking the target near the top versus not finding the target at all.**

Finally, there are a very small handful of low-quality queries (i.e. those which do not have a mode around low-number ranks): 8, 35, 37, 78. We'll keep these in mind, as we may decide to treat them as outlier and filter their results out when determining the best methodology. Of course, we will include them when reporting the performance of the methodology that we determine to be the best.

In [27]:
outlier_ids = [8,35,37,78];

Now, we can begin to investigate how the various properties of the queries and their targets affect the average performance of retrieval. We'll start out by looking at query length. I think it may make more sense to examine the median rank over all experiments rather than the mean because otherwise, experiments in which the targets were not retrieved may exert undue influence on the results.

In [28]:
outlier_mask = [1:length(QUERIES)...] .∈ [outlier_ids]

query_lengths = [length(query["text"]) for query in QUERIES]
med_query_ranks = [median(coalesce.(ranking_results[ranking_results[:,"query_id"].==q_id,"target_rank"],731))
        for q_id in 1:length(QUERIES)]
tooltips = ["Q$(i): $(query["text"])<br />Median rank: $(med_query_ranks[i])"
    for (i,query) in enumerate(QUERIES)]

r = (
    round(cor(query_lengths[(!).(outlier_mask)],med_query_ranks[(!).(outlier_mask)]),digits=3),
    round(cor(query_lengths,med_query_ranks),digits=3)
)
ρ = (
    round(corspearman(query_lengths[(!).(outlier_mask)],med_query_ranks[(!).(outlier_mask)]),digits=3),
    round(corspearman(query_lengths,med_query_ranks),digits=3)
)

println("""Linear correlation: $(r[1]) ($(r[2]) including outliers)""")
println("""Rank correlation: $(ρ[1]) ($(ρ[2]) including outliers)""")

scatter(
    query_lengths[(!).(outlier_mask)],
    med_query_ranks[(!).(outlier_mask)],
    xlabel = "Length (Characters)",
    ylabel = "Median Rank",
    title = "Median Rank vs Query Length",
    hover = tooltips[(!).(outlier_mask)],
    label = "Successful Query"
)

scatter!(
    query_lengths[(outlier_mask)],
    med_query_ranks[(outlier_mask)],
    hover = tooltips[(outlier_mask)],
    label = "Outlier Query"
)

Linear correlation: -0.18 (-0.083 including outliers)
Rank correlation: -0.167 (-0.134 including outliers)


Most of the queries have a very low median rank, which indicates that over half of the methodologies are actually quite successful for most of the queries. 

Ignoring the outlier queries for a moment, we do see a slight negative trend between query length and median target rank along the upper envelope of this graph. If we zoom in to the range of ranks 1 to 100, we can see a similar thing. My interpretation of this is that retrieval is "more consistently good" or "more reliable" when using longer queries. 

In order to get a better sense of how the aspects of the TikToks themselves affect retrieval performance, I watched all of the query targets and manually labeled them with the following 5 subjective binary attributes:

- `useful description`: If a human were to look at the description, would it help them to remember the video? Does the description use keywords from the video?
- `comments-on-topic`: Do the comments use keywords from or related to the video?
- `important-lyrics`: Does the music play a central role in delivering the message of the video? Would a user derive search terms from the lyrics of the music?
- `subtextual`: Is the message of the video indirect? Does the video make a reference or an inside joke? Does the videoo require information from outside the video to understand?
- `purely-visual`: Does the video lack any kind of dialogue or narration?

To better understand how these attributes affect retrieval, let's look at the difference between median retrieval with and without each attribute being true. Note that the results we report will be the average over all queries matching a given attribute of those queries' median target ranks over all experiments. 

I will again remove the queries that were judged to be of poor quality, because I don't want them to skew our understanding of the broader effects.

We should repeat this analysis of target properties using only the best retrieval methodology, once we've determined what that happens to be.

In [29]:
target_attributes = ["useful_description","comments_on_topic",
    "important_lyrics","subtextual","purely_visual"];

grouped = groupby(ranking_results[:,
        vcat(["query_id","target_rank"],target_attributes)],"query_id")

missingmedian = ranks -> median(coalesce.(ranks,731))

query_medians = combine(grouped, "target_rank" => missingmedian .=>"median_target_rank",
    target_attributes.=>first.=>target_attributes, ungroup=false) |> DataFrame;
#When grouping by query, all the attributes will be consistent across a group, so
#we just take the first value since they're all the same.    

In [30]:
outlierless_mask = query_medians[:,"query_id"]  .∉ [outlier_ids]

p1 = bar(
    [mean(coalesce.(query_medians[
        outlierless_mask .&& query_medians[:,attribute].==true,"median_target_rank"],731))
    for attribute in target_attributes],
    xticks = (1:length(target_attributes), target_attributes),
    xrotation = 15,
    title = "With Attribute",
    xlabel = "Attribute",
    ylabel = "Median Target Rank",
    legend = false
)

p2 = bar(
    [mean(coalesce.(query_medians[
        outlierless_mask .&& query_medians[:,attribute].==true,"median_target_rank"],731))-
    mean(coalesce.(query_medians[
        outlierless_mask .&& query_medians[:,attribute].==false,"median_target_rank"],731))
    for attribute in target_attributes],
    xticks = (1:length(target_attributes), target_attributes),
    title = "Difference: With - Without",
    xrotation = 15,
    xlabel = "Attribute",
    ylabel = "Difference in Median Target Rank",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,450),
    plot_title = "Retrieval Performance vs Attributes of Target Videos")


These results strongly affirm our hypotheses about the challenges of TikTok retrieval. Targets with a useful description have the highest average rank, while targets that are subtextual or purely visual in nature have the lowest. 

I hesitate to try to draw any more conclusions from this chart because the attributes themselves may have interdependencies, and further more, it is difficult to make connections to the retrieval methodology because these results are averaged (median) over all of our experiments.

## Performance vs Cosine Scoring Formulas <a id="anal-formulas"></a>
### [^Contents](#contents)

Now, let's investigate how the different formulas for computing document vectors in the cosine scoring process impacted the search results. 

In [31]:
all_experiments = sql[:all] = """
    SELECT * FROM 
    (SELECT * FROM indexes RIGHT JOIN experiments ON indexes.index_id=experiments.index_id)
    indexes_and_experiments
    RIGHT JOIN ($(sql[:ranking_results])) ranks_and_queries
        ON indexes_and_experiments.experiment_id = ranks_and_queries.experiment_id""";
#Complete atomic records.

db = SQLite.DB("results.db")
all_data = DBInterface.execute(db,sql[:all]) |> DataFrame
DBInterface.close!(db)
println(size(all_data))
first(all_data,3)

(82560, 27)


3×27 DataFrame
 Row │ index_id  ngram_size  sr     ocr    comments  field_attributions  indexing_time  storage  vocab_size  experiment_id  index_id:1  term_weight  collection_weight  normalizer  experiment_id_1  query_id  retrieval_time  target_rank  query_id:1  query_text                    target_id            author  useful_description  comments_on_topic  purely_visual  important_lyrics  subtextual 
     │ Int64     Int64?      Int64  Int64  Int64     Int64               Float64        Int64    Int64       Int64          Int64       String       String             String      Int64            Int64     Float64         Int64?       Int64       String                        String               String  Int64               Int64              Int64          Int64             Int64      
─────┼────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │        1     missing      0      0         0                   1       0.421693  2634195       11272              1           1  b            x                  x                         1         1        0.189629            1           1  D&D players stairs door       7171982974357966122  jim                      0                  1              0                 0           0
   2 │        1     missing      0      0         0                   1       0.421693  2634195       11272              1           1  b            x                  x                         1         2        7.6e-5        missing           2  knight besties sword fight    7144411926246935854  jim                      0                  1              1                 0           0
   3 │        1     missing      0      0         0                   1       0.421693  2634195       11272              1           1  b            x                  x                         1         3        7.36e-5       missing           3  football dad musical theater  7052789831151193391  jim                      1                  1              0                 0           0

We'll start out by examining the median, grouped by formula, of the averge (over all indexing methodologies) of all the well-formed queries.

In [32]:
all_data[!,"formula"] = [join(row) 
    for row in eachrow(all_data[:,["term_weight","collection_weight","normalizer"]])]
all_data;

In [33]:
all_outlierless_mask = (all_data[:,"query_id"] .∉ [outlier_ids])

formula_attributes = ["term_weight","collection_weight","normalizer"];

grouped = groupby(all_data[all_outlierless_mask,vcat("formula","target_rank")],"formula")

missingmedian = ranks -> median(coalesce.(ranks,731))
count1 = ranks -> mean(coalesce.(ranks,731).==1)

formula_results = combine(grouped, 
    "target_rank" => missingmedian .=>"median_target_rank",
    "target_rank" => count1 .=>"targets_ranked_1",
    ungroup=false) |> DataFrame;
#When grouping by query, all the attributes will be consistent across a group, so
#we just take the first value since they're all the same.

Since there are only 12 formulas, I am going to look at the results. After running this once, I've decided to add two more metrics by which to evaluate the formulas: fraction of queries whose targets were ranked 1 (over all indexing methods).

In [34]:
sort!(formula_results,["median_target_rank","targets_ranked_1"],rev=[false,true]);
formula_results

12×3 DataFrame
 Row │ formula  median_target_rank  targets_ranked_1 
     │ String   Float64             Float64          
─────┼───────────────────────────────────────────────
   1 │ bpx                     2.0          0.468902
   2 │ bfx                     2.0          0.468293
   3 │ bxx                     2.0          0.454878
   4 │ bxc                     2.0          0.454878
   5 │ tpx                     2.0          0.408079
   6 │ tfx                     2.0          0.40625
   7 │ txx                     3.0          0.355945
   8 │ txc                     3.0          0.348476
   9 │ tpc                     6.0          0.258841
  10 │ bpc                     8.0          0.233841
  11 │ tfc                    14.0          0.189329
  12 │ bfc                    19.0          0.168598

In [35]:
p1 = bar(
    formula_results[:,"median_target_rank"],
    xticks = (1:length(formula_results[:,"formula"]), formula_results[:,"formula"]),
    title = "Median Target Rank vs Formula",
    xlabel = "Formula",
    ylabel = "Median Target Rank",
    legend = false
)

p2 = bar(
    formula_results[:,"targets_ranked_1"],
    xticks = (1:length(formula_results[:,"formula"]), formula_results[:,"formula"]),
    title = "Targets Ranked 1 vs Formula",
    xlabel = "Formula",
    ylabel = "Fraction of Targets Ranked 1",
    legend = false,
    ylim=(0,1)
)

plot([p1,p2]..., layout=(1,2), size=(900,400),
    plot_title = "Retrieval Performance vs Document Vector Formula")


The most obvious effect we can see here is that 6 of the top 7 formulas all use no normalization whereas the bottom 5 formulas all use Euclidean normalization. There is a very good explanation for this: all of the fields from which text was derived can very vastly in length, between no content and lots of content. Videos themselves can be as short as a few seconds or as long as several minutes. Although the idea of normalization is to allow short documents to get equal consideration, in this case, it serves to penalize documents with more searchable information.

Consider the following query and documents:

    QUERY: "the one piece is real"
    DOC 1: "the one piece"
    DOC 2: "the one piece is real comment comment comment comment comment"

Clearly, we are trying to find DOC 2, however, using binary weighting and no collection frequency weighting with Euclidean document vector normalization, DOC 1 gets a score of $3/\sqrt{3}\approx 1.72$, while DOC 2 gets a score of $5/\sqrt{10}\approx 1.58$.

The top four formulas all use binary term weighting, so I suppose that this is the best way to account for differences in length. 

Looking at the results for the formulas that use no normalization, if we group by term weighting factor, we can see that the ranking goes p > f > x. In other words, the collection frequency factor is important, and it appears that probabilistic IDF is slightly better than regular IDF.

Here is my interpretation of these results. This corpus of TikToks contains content of varying length that accounts for a very diverse set of topics. More mentions of a query term does not equate to more relevance, becauase some videos are simply longer than others, and they will naturally mention their keywords more total times. Normalization cannot be used to account for this because differences in length are not only due to relative "amounts" of main content but also the lengths of description text, comments, etc. Additionally, not all words are useful as keywords; probabilistic IDF happens to work well for weighting words based on their rarity in the corpus.  




## Performance vs Indexing Methods <a id="anal-indexing"></a>
### [^Contents](#contents)

Finally, we will examine how different indexing methodologies impacted retrieval performance. We'll start out by examining the additional text features. For this analysis, we'll only use records that use the "bpx" formula, so that we can focus on finding the best of the best. Let's start by simply looking at the top handful of results

In [36]:
all_outlierless_mask = (all_data[:,"query_id"] .∉ [outlier_ids])
bpx_mask = (all_data[:,"formula"] .== "bpx")
index_attributes = ["ngram_size","sr","ocr","comments","field_attributions"]

grouped = groupby(all_data[all_outlierless_mask .&& bpx_mask,
        vcat(index_attributes,["index_id","target_rank"])],"index_id")

missingmedian = ranks -> median(coalesce.(ranks,731))
missingmean = ranks -> mean(coalesce.(ranks,731))
count1 = ranks -> mean(coalesce.(ranks,731).==1)
countmissing = ranks -> mean(ismissing.(ranks))

index_results = combine(grouped, 
    "target_rank" => missingmedian .=>"median_target_rank",
    "target_rank" => missingmean .=>"mean_target_rank",
    "target_rank" => count1 .=>"targets_ranked_1",
    "target_rank" => countmissing .=>"targets_missed",
    index_attributes .=> first .=> index_attributes,
    ungroup=false) |> DataFrame;
#When grouping by query, all the attributes will be consistent across a group, so
#we just take the first value since they're all the same.  

In [37]:
sort!(index_results,["targets_ranked_1","targets_missed"],rev=[true,false]);
first(index_results,10)

10×10 DataFrame
 Row │ index_id  median_target_rank  mean_target_rank  targets_ranked_1  targets_missed  ngram_size  sr     ocr    comments  field_attributions 
     │ Int64     Float64             Float64           Float64           Float64         Int64?      Int64  Int64  Int64     Int64              
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │       77                 1.0           12.0244          0.695122       0.0                 4      1      1         1                   0
   2 │       78                 1.0           10.439           0.695122       0.0                 5      1      1         1                   0
   3 │       47                 1.0           20.3537          0.670732       0.0                 4      1      0         1                   0
   4 │       48                 1.0           20.378           0.670732       0.0                 5      1      0         1                   0
   5 │       79                 1.0           37.878           0.634146       0.0243902           6      1      1         1                   0
   6 │       68                 1.0           11.1585          0.621951       0.0                 5      0      1         1                   0
   7 │       67                 1.0           11.3537          0.609756       0.0                 4      0      1         1                   0
   8 │       71                 1.0           26.8415          0.609756       0.0243902     missing      1      1         1                   1
   9 │       28                 1.0           21.5732          0.597561       0.0                 5      0      0         1                   0
  10 │       74                 1.0           29.7439          0.597561       0.0243902           6      1      1         1                   1

Of the top 10 indexes, here are the important trends to notice:
- 9 of 10 use n-grams, of which four use 5-grams, three use 4-grams, two use 6-grams, and none use 7-grams.
- 9 of 10 use two or more extra text features, of which five use all three extra text features
    - 10/10 use comments
    - 7/10 use speech recognition text
    - 7/10 use coverphoto OCR text
- Only 2/10 use field attributions
- Indexes that used 4- or 5-gram tokenization did not miss any targets; indexes that used 6-gram or word tokenization missed a smal handful of targets.

Now, let's take a closer look at how the additional text sources affect retrieval performance.

In [38]:
sr_mask = (index_results[:,"sr"].==1)
ocr_mask = (index_results[:,"ocr"].==1)
c_mask = (index_results[:,"comments"].==1)

p1 = bar(
    [
        mean(index_results[(!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"targets_ranked_1"]),
        mean(index_results[(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"targets_ranked_1"]),
        mean(index_results[(!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),"targets_ranked_1"]),
        mean(index_results[(!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),"targets_ranked_1"]),
        mean(index_results[(sr_mask).&&(ocr_mask).&&(!).(c_mask),"targets_ranked_1"]),
        mean(index_results[(sr_mask).&&(!).(ocr_mask).&&(c_mask),"targets_ranked_1"]),
        mean(index_results[(!).(sr_mask).&&(ocr_mask).&&(c_mask),"targets_ranked_1"]),
        mean(index_results[(sr_mask).&&(ocr_mask).&&(c_mask),"targets_ranked_1"])
    ],
    xticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    title = "Targets Ranked 1 vs Features",
    xlabel = "Extra Features",
    ylabel = "Avg Fraction of Targets Ranked 1",
    legend = false
)

p2 = bar(
    [
        mean(index_results[(!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"targets_missed"]),
        mean(index_results[(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),"targets_missed"]),
        mean(index_results[(!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),"targets_missed"]),
        mean(index_results[(!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),"targets_missed"]),
        mean(index_results[(sr_mask).&&(ocr_mask).&&(!).(c_mask),"targets_missed"]),
        mean(index_results[(sr_mask).&&(!).(ocr_mask).&&(c_mask),"targets_missed"]),
        mean(index_results[(!).(sr_mask).&&(ocr_mask).&&(c_mask),"targets_missed"]),
        mean(index_results[(sr_mask).&&(ocr_mask).&&(c_mask),"targets_missed"])
    ],
    xticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    title = "Targets Missed vs Features",
    xlabel = "Extra Features",
    ylabel = "Avg Fraction of Targets Missed",
    legend = false
)

plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Retrieval Performance vs Extra Features")

The chart on the left shows that if only one additional source of text is to be included, the best choice is comments, followed by speech recognition text, then coverphoto text. Interestingly, we can see that SR and OCR together are on par with comments alone. The best two features to use SR and comments, while the combination of all three features to enrich the basic text is overall the best. 

On average, using only basic text, only ~25% of queries find their target at rank 1. In comparison, supplementing the basic text with speech recognition, OCR, and comments, boosts this to nearly 60%. This undeniably supports our hypothesis that using these additional text features would have a strong positive impact on retrieval performance.

The chart on the left tells a similar story; over 40% of queries completely missed their target when using only the basic information. Of the three features, comments provided the best improvement, with only ~5% of fractions missing their targets. Adding speech recognition and coverphoto OCR almost halves the win rate compared to using comments alone.

Now, let's take a look at n-grams.

In [39]:
nogram_mask = (ismissing.(index_results[:,"ngram_size"]))
gram4_mask = coalesce.(index_results[:,"ngram_size"].==4,false)
gram5_mask = coalesce.(index_results[:,"ngram_size"].==5,false)
gram6_mask = coalesce.(index_results[:,"ngram_size"].==6,false)
gram7_mask = coalesce.(index_results[:,"ngram_size"].==7,false)
#Bitwise operators on missing values return missing, so we fill them in with false.


p1 = bar(
    [
        mean(index_results[nogram_mask,"targets_ranked_1"]),
        mean(index_results[gram4_mask,"targets_ranked_1"]),
        mean(index_results[gram5_mask,"targets_ranked_1"]),
        mean(index_results[gram6_mask,"targets_ranked_1"]),
        mean(index_results[gram7_mask,"targets_ranked_1"])
    ],
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    title = "Targets Ranked 1 vs Tokenization",
    xlabel = "Method",
    ylabel = "Avg Fraction of Targets Ranked 1",
    legend = false
)

p2 = bar(
    [
        mean(index_results[nogram_mask,"targets_missed"]),
        mean(index_results[gram4_mask,"targets_missed"]),
        mean(index_results[gram5_mask,"targets_missed"]),
        mean(index_results[gram6_mask,"targets_missed"]),
        mean(index_results[gram7_mask,"targets_missed"])
    ],
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    title = "Targets Missed vs Tokenization",
    xlabel = "Method",
    ylabel = "Avg Fraction of Targets Missed",
    legend = false
)

plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Retrieval Performance vs Tokenization Method")

On the left, it appears that there is a tie between 4-grams and 5-grams for the best tokenization method, followed by a tie between words and 6-grams, and then finally 7-grams. However, if we look at the chart on the right, that is clearly not the case; word tokenization missed nearly twice as many targets as 6-gram tokenization and around 4x as many as 5-gram tokenization.

Of all tokenization methods, it appears that 4-gram tokenization most consistently finds the query targets and ranks them at the top of the list. These results are consistent with the results of a study by Mayfield and McNamee ([Character N-Gram Tokenization for European
Language Text Retrieval](https://link.springer.com/article/10.1023/B:INRT.0000009441.78971.be)). It appears that 4-grams best account for morphological variations and misspellings.

Now, let's take a look at the heatmaps to see the interaction between tokenization method and extra text.

In [40]:
first_vs_tokenization_and_features = [
    mean(index_results[feature_mask.&&tokenization_mask,"targets_ranked_1"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]

missed_vs_tokenization_and_features = [
    mean(index_results[feature_mask.&&tokenization_mask,"targets_missed"])
    for feature_mask in (
        (!).(sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (!).(sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(!).(c_mask),
        (sr_mask).&&(!).(ocr_mask).&&(c_mask),
        (!).(sr_mask).&&(ocr_mask).&&(c_mask),
        (sr_mask).&&(ocr_mask).&&(c_mask)
    ), 
    tokenization_mask in (nogram_mask,gram4_mask,gram5_mask,gram6_mask,gram7_mask)
]



p1 = heatmap(
    first_vs_tokenization_and_features,
    yticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Avg Targets Ranked First",
    ylabel = "Extra Features",
    xlabel = "Tokenization"
)

p2 = heatmap(
    missed_vs_tokenization_and_features,
    yticks = (1:8, ["none","sr","ocr","c","sr+ocr","sr+c","ocr+c","sr+ocr+c"]),
    xticks = (1:5, ["word","4-gram","5-gram","6-gram","7-gram"]),
    yflip = true,
    #guide_position = :top,
    title = "Avg Missed Targets",
    ylabel = "Extra Features",
    xlabel = "Tokenization"
)


plot([p1,p2]..., layout=(1,2), size=(900,400), 
    plot_title = "Retrieval Performance vs Tokenization & Extra Features")

It appears that the features are mostly independent; the major conclusions we made from our bar charts still hold true when looking at any individual row or column of these charts. However, we can see that with fewer sources of extra text, 4-grams more consistently rank targets in 1st place, whereas with more extra text, 5-grams are slightly better. This trend perfectly mirrors the miss rate; 5-grams are more prone to missing short keywords or keywords with short morphological stems. When there is less text to index, 4-grams miss fewer keywords, whereas when there is more text to index, 5-grams are better able to filter out false matches.

Now, let's take a look at field attributions. We only saw a single index that used them in the top 10 indexes, so that should form our expectations. The number of missed targets will be the same regardless of whether we use field attributions or not, so instead with our second plot, let's compare with vs without attributions for only 4- and 5-grams using sr+ocr+c to index.

In [41]:
attribution_mask = (index_results[:,"field_attributions"].==1)
best_mask = (coalesce.(index_results[:,"ngram_size"],-1).∈[[4,5]]
    ).&&(sr_mask).&&(ocr_mask).&&(c_mask)

p1 = bar(
    [
        mean(index_results[(!).(attribution_mask),"targets_ranked_1"]),
        mean(index_results[(attribution_mask),"targets_ranked_1"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "All Indexes",
    xlabel = "Field Attributions",
    ylabel = "Avg Fraction of Targets Ranked 1",
    legend = false
)

p2 = bar(
    [
        mean(index_results[(!).(attribution_mask).&&best_mask,"targets_ranked_1"]),
        mean(index_results[(attribution_mask).&&best_mask,"targets_ranked_1"])
    ],
    xticks = (1:2, ["without","with"]),
    title = "Only 4- or 5-gram & SR+OCR+C",
    xlabel = "Field Attributions",
    ylabel = "Avg Fraction of Targets Ranked 1",
    legend = false
)


plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "Retrieval Performance vs Field Attributions")

It's possible that we may see different results were we to use different combinations of field attributions rather than all or nothing, but these results indicate that when it is all or nothing, it's best to not use field attributions.

Field attributions are generally useful when keywords should be weighted differently based on the field in which they occur. It appears that this is not the case for the TikToks; a keyword has about the same value regardless of whether if it occurs in the basic info, the speech-to-text, the coverphoto, or the top comments. So, in this case, field attributions only screw up the idf calculations, which hurts performance.  

At this point, all we have left to do is break the tie between 4-grams and 5-grams.

In [42]:
sort!(index_results,["targets_ranked_1","targets_missed"],rev=[true,false]);
first(index_results,2)

2×10 DataFrame
 Row │ index_id  median_target_rank  mean_target_rank  targets_ranked_1  targets_missed  ngram_size  sr     ocr    comments  field_attributions 
     │ Int64     Float64             Float64           Float64           Float64         Int64?      Int64  Int64  Int64     Int64              
─────┼──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
   1 │       77                 1.0           12.0244          0.695122             0.0           4      1      1         1                   0
   2 │       78                 1.0           10.439           0.695122             0.0           5      1      1         1                   0

When using all sources of text and no field attributions, both 4-grams and 5-grams have a miss rate of 0 and an equal rate of ranking the target in first place (~70%). The mean target rank is slightly lower with 5-grams because they are more distinguishing, and the queries are about 5x faster with 5-grams than 4-grams. On the other hand, the 4-gram index only requires about 80% as much storage as the 5-gram index, and they are less likely to miss a document with a small amount of text.

In order to break the tie, I want to compare their performance based on target attributes.

In [43]:
gram4_mask = coalesce.(all_data[:,"ngram_size"],-1).==4
gram5_mask = coalesce.(all_data[:,"ngram_size"],-1).==5
outlierless_mask = all_data[:,"query_id"]  .∉ [outlier_ids]
best_mask = (all_data[:,"field_attributions"].==0).&&(all_data[:,"sr"].==1).&&
    (all_data[:,"ocr"].==1).&&(all_data[:,"comments"].==1).&&
    (all_data[:,"formula"].=="bpx").&&(gram4_mask.||gram5_mask)

best_query_results = all_data[outlierless_mask.&&best_mask,:];

In [44]:
p1 = groupedbar(
    repeat(target_attributes,2),
    vcat(
        [mean(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes],
        [mean(best_query_results[best_query_results[:,"ngram_size"].==5 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes]
    ), 
    group = repeat(["4-gram","5-gram"],inner=length(target_attributes)),
    hover = ["N = $(n)" for n in vcat(
        [length(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes],
        [length(best_query_results[best_query_results[:,"ngram_size"].==5 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes]
    )],
    ylabel="Average Rank of Retrieval Target",
    xlabel="Target Attribute",
    xrotation = 15,
    title="With Attribute",
    size=(700,400)
)

p2 = groupedbar(
    repeat(target_attributes,2),
    vcat(
        [mean(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) - 
        mean(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==false,"target_rank"])
            for attribute in target_attributes],
        [mean(best_query_results[best_query_results[:,"ngram_size"].==5 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) -
        mean(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==false,"target_rank"])
            for attribute in target_attributes]
    ), 
    group = repeat(["4-gram","5-gram"],inner=length(target_attributes)),
    hover = ["N = $(n) vs $(length(QUERIES)-n)" for n in vcat(
        [length(best_query_results[best_query_results[:,"ngram_size"].==4 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes],
        [length(best_query_results[best_query_results[:,"ngram_size"].==5 .&& 
        best_query_results[:,attribute].==true,"target_rank"]) 
            for attribute in target_attributes]
    )],
    ylabel="Difference in Average Rank of Retrieval Target",
    xlabel="Target Attribute",
    xrotation = 15,
    title="Difference: With - Without",
    size=(700,400)
)

plot([p1,p2]..., layout=(1,2), size=(900,400), plot_title = "4-gram vs 5-gram Performance by Target Attributes")

It looks like the 4-gram index performs much better when the target video is subtextual in nature or incorporates the music as a part of the message. This is actually quite strange, so I'm going to take a closer look at these queries to see what I can glean.

In [45]:
lyricssubtext = best_query_results[
    ((best_query_results[:,"important_lyrics"].==true).||
    (best_query_results[:,"subtextual"].==true)),
    ["query_text","ngram_size","target_rank"]]

lyricssubtext_4v5 = DataFrame(Dict(
    "query_text" => unique(lyricssubtext[:,"query_text"]),
    "rank_4gram" => lyricssubtext[lyricssubtext[:,"ngram_size"].==4,"target_rank"],
    "rank_5gram" => lyricssubtext[lyricssubtext[:,"ngram_size"].==5,"target_rank"]
))

lyricssubtext_4v5[(!).(lyricssubtext_4v5[:,"rank_5gram"].==lyricssubtext_4v5[:,"rank_4gram"]),:]

5×3 DataFrame
 Row │ query_text                         rank_4gram  rank_5gram 
     │ String                             Int64?      Int64?     
─────┼───────────────────────────────────────────────────────────
   1 │ dio jojo girl mask                          4          10
   2 │ slapaphone, friends theme, rolli…           8         179
   3 │ Will Smith fish tales, Chris Roc…           2           1
   4 │ camera still on zoom                        6           3
   5 │ Chrissy Wake up shakespeare                 4          10

There are only 5 queries for which the performance of 4-grams and 5-grams differs. With "dio jojo girl mask" and "chrissy wake up shakespeare", the query terms that match the target text are just short. With "slapaphone, friends theme, rolling in the deep", I really have no clue what happened. In the other two examples, the 5-gram index beat the 4-gram index.

Although this is a really small handful of examples to use as a tiebreaker, I am going to rule in favor of 4-grams. When we enrich TikToks with information from the title, speech recognition, and top comments, the differences between 4-gram and 5-gram indexes are slim, but when keywords in the query are short, 4-grams will win. 

Next, I want to examine how target length impacts retrieval results with 4-grams.

In [46]:
best_results = all_data[best_mask.&&gram4_mask,:]

ids = [row["target_id"] for row in eachrow(best_results)]
ranks = [row["target_rank"] for row in eachrow(best_results)]
tooltips = ["$(row["query_id"]): $(row["query_text"])<br />Rank: $(row["target_rank"])"
    for row in eachrow(best_results)]

desc_lengths = [length(TIKTOKS[id]["description"]) for id in ids]
c_lengths = [length(TIKTOKS[id]["comment-text"]) for id in ids]
sr_lengths = [length(TIKTOKS[id]["speech-to-text"]) for id in ids]
ocr_lengths = [length(TIKTOKS[id]["coverphoto-ocr"]) for id in ids]

plots = [
    scatter(
        desc_lengths,
        ranks,
        xlabel = "Length (Characters)",
        ylabel = "Rank",
        title = "Description",
        hover = tooltips,
        alpha = 0.3
    ),
    scatter(
        c_lengths,
        ranks,
        xlabel = "Length (Characters)",
        ylabel = "Rank",
        title = "Comments",
        hover = tooltips,
        alpha = 0.3
    ),
    scatter(
        sr_lengths,
        ranks,
        xlabel = "Length (Characters)",
        ylabel = "Rank",
        title = "Speech Recognition",
        hover = tooltips,
        alpha = 0.3
    ),
    scatter(
        ocr_lengths,
        ranks,
        xlabel = "Length (Characters)",
        ylabel = "Rank",
        title = "Optical Character Recognition",
        hover = tooltips,
        alpha = 0.3
    )
]

plot(plots..., layout=(2,2), size=(900,900), plot_title = "Retrieval Performance vs Target Length")

It appears that there are only 6 queries that did not rank the relevant documents in the top ~25; all four of the queries that we judged to be poor quality are present in this set. 

It's possible that shorter speech reconition and/or OCR fields are associated trend with worse target rank, however this may just be an artifact caused by the fact that the majority of targets have relatively short SR/OCR fields and there is only a small handful of really poor performances. 

Finally, I want to be able to report the fraction of queries whose target ranked in the top N results for every value of N.

In [47]:
ranks_ = collect(keys(proportionmap(ranks)))
counts_ = collect(values(proportionmap(ranks)))
order = sortperm(ranks_)

plot(
    ranks_[order],
    cumsum(counts_[order]),
    title = "Proportion of Query Targets Ranked in Top-N",
    xlabel = "N",
    ylabel = "Proportion of Targets",
    legend = false,
    ylims=(0,1)
)

Impressively, 90% of the queries ranked in the top 8 search results.

## Conclusion <a id="conclusion"></a>
### [^Contents](#contents)

In this study, we searched for optimal conditions for single-target TikTok retrieval by investigating four aspects of the retrieval process: tokenization, the use of additional text features, field attributions, and document vector formulas. Our hypotheses were largely supported by the evidence. 

We hypothesized that no normalization could be better than Euclidean normalization because Euclidean distance may penalize documents whose keywords are more diluted by irrelevat information (e.g. off-topic comments, unhelpful descriptions, etc.), and we found this to be the case. Additionally, we believed that binary term weighting may be more useful because raw term weighting can mistakenly favor longer videos; this hypothesis was also supported. Finally, we hypothesized that it was best to use a collection frequency term, and we found that probabilistic IDF was best.


As hypothesized, small n-gram (n = 4,5) tokenization provided much more robust performance than word-based tokenization. We believe that using n-grams accounts for different morphological forms of query terms as well as typos, which is why n-gram based indexing and search generally resulted in a ~4x lower miss rate than a word-based approach. Although 4-grams result in ~5x slower queries than 5-grams, 4-grams tend to yield better performance for short keywords and targets with few keywords. 

We were very optimistic that retrieval performance could be greatly improved by including text from top comments, text extracted from the video using text-to-speech, and/or text extracted from the coverphoto with optical character recognition. Our results that including any of these additional sources will provide an increase over the baseline, but of the three, top comments are the most useful — as useful as both speech recognition and optical character recognition combined. We found that the biggest differences in average target rank are between those with and without on-topic comments, and between those with and without useful descriptions. We had worried that off-topic comments may reduce precision, but despite this, comments were the most useful additional feature to include. All three extra text sources together gave the best results.

We explored field attributions with the hope that it might help offset accidentially retrieving documents whose comments are off-topic. However, due to the topical diversity of the corpus, most off-topic comments were not relevant to other documents, so field attributions did not end up being useful. 


Our best retrieval methodology exhibited excellent results; 90% of queries had their relevant video ranked in the top 8. However, only 2/3 of the queries had their relevant video ranked 1st, which indicates that there is still much room for improvement. 

Because TikTok's desktop site displays comments in a semi-random order, the "top" comments that were scraped were not necessarily the most liked or those with the most replies. Because useful comments make a strong positive impact on retrieval performance, we could likely achieve even better results by using the top-liked or top-replied comments to index on.

Since useful descriptions also improve retrieval performance, TikTok should consider recommending to its content creators that they write descriptions that summarize the content using keywords rather than just using popular hashtags, which do not really help specific-video search. Another possible direction to explore is video content analysis, which may be able to somewhat automate or assist description writing.

The speech recognition and optical character recognition tools I used are out-of-the-box Python modules. I only used the default settings, and did not closely investigate the quality of the results. On the other hand, TikTok has developed a very robust speech-to-text system that is used to generate closed-captions for videos on their platform. The text is already extracted; it just needs to be incorporated in the index. As an enterprise-level company, they are certainly capable of developing or acquiring a robust OCR system too.

We must acknowledge the difference in scale between this corpus of <1500 videos and the entire TikTok platform, which is estimated to see millions of videos posted per day. However, in the context of specific-video search, the number of videos that must be searched can be massively reduced by only searching through the pool of videos that the searcher has watched. In practice, specific-video search may be improved on the platform by weighting videos in proportion to how recently the searcher has watched them, if at all.
